# California housing prices 
.
Versão com o PySpark do kernel [California housing prices](https://github.com/robson-rsp/datascience/blob/main/regression/california_housing_prices.ipynb). Este notebook foi escrito no ambiente do Databricks e exportado como arquivo IPython .ipynb. Os textos daqui são cópias dos originais do link.
---
A tarefa neste kernel é criar um modelo de Machine Learning que estime preços de imóveis no estado da Califórnia baseado em características, como:

*   latitude/longitude: Localização do imóvel
*   housing_median_age: Idade média dos imóveis naquela quadra
*   totalRooms: Número total de cômodos dentro de um quarteirão
*   totalBedrooms: Número total de quartos dentro de um quarteirão
*   population: Número total de pessoas que moram em uma quadra
*   households: Número total de habitações em uma quadra
*   medianIncome: Renda média das famílias de uma quadra (medida em dezenas de milhares de dólares americanos)
*   medianHouseValue: Valor médio dos imóveis de uma quadra (medido em dólares americanos)
*   oceanProximity: Localização do imóvel em relação ao oceano/mar

Obs. A média populacional desses quarteirões é de 600 até 3000 pessoas.

Fonte: [Kaggle](https://www.kaggle.com/datasets/camnugent/california-housing-prices)

In [0]:

housing = spark.read.format("csv") \
          .option("inferSchema", "True") \
          .option("header", "True") \
          .option("sep", ",") \
          .load("/FileStore/tables/housing.csv")

# EDA

In [0]:
display(housing)

longitude latitude housing_median_age total_rooms total_bedrooms population households median_income median_house_value ocean_proximity -122.23 37.88 41.0 880.0 129.0 322.0 126.0 8.3252 452600.0 NEAR BAY -122.22 37.86 21.0 7099.0 1106.0 2401.0 1138.0 8.3014 358500.0 NEAR BAY -122.24 37.85 52.0 1467.0 190.0 496.0 177.0 7.2574 352100.0 NEAR BAY -122.25 37.85 52.0 1274.0 235.0 558.0 219.0 5.6431 341300.0 NEAR BAY -122.25 37.85 52.0 1627.0 280.0 565.0 259.0 3.8462 342200.0 NEAR BAY -122.25 37.85 52.0 919.0 213.0 413.0 193.0 4.0368 269700.0 NEAR BAY -122.25 37.84 52.0 2535.0 489.0 1094.0 514.0 3.6591 299200.0 NEAR BAY -122.25 37.84 52.0 3104.0 687.0 1157.0 647.0 3.12 241400.0 NEAR BAY -122.26 37.84 42.0 2555.0 665.0 1206.0 595.0 2.0804 226700.0 NEAR BAY -122.25 37.84 52.0 3549.0 707.0 1551.0 714.0 3.6912 261100.0 NEAR BAY -122.26 37.85 52.0 2202.0 434.0 910.0 402.0 3.2031 281500.0 NEAR BAY -122.26 37.85 52.0 3503.0 752.0 1504.0 734.0 3.2705 241800.0 NEAR BAY -122.26 37.85 52.0 2491.0 474.0 1098.0 468.0 3.075 213500.0 NEAR BAY -122.26 37.84 52.0 696.0 191.0 345.0 174.0 2.6736 191300.0 NEAR BAY -122.26 37.85 52.0 2643.0 626.0 1212.0 620.0 1.9167 159200.0 NEAR BAY -122.26 37.85 50.0 1120.0 283.0 697.0 264.0 2.125 140000.0 NEAR BAY -122.27 37.85 52.0 1966.0 347.0 793.0 331.0 2.775 152500.0 NEAR BAY -122.27 37.85 52.0 1228.0 293.0 648.0 303.0 2.1202 155500.0 NEAR BAY -122.26 37.84 50.0 2239.0 455.0 990.0 419.0 1.9911 158700.0 NEAR BAY -122.27 37.84 52.0 1503.0 298.0 690.0 275.0 2.6033 162900.0 NEAR BAY -122.27 37.85 40.0 751.0 184.0 409.0 166.0 1.3578 147500.0 NEAR BAY -122.27 37.85 42.0 1639.0 367.0 929.0 366.0 1.7135 159800.0 NEAR BAY -122.27 37.84 52.0 2436.0 541.0 1015.0 478.0 1.725 113900.0 NEAR BAY -122.27 37.84 52.0 1688.0 337.0 853.0 325.0 2.1806 99700.0 NEAR BAY -122.27 37.84 52.0 2224.0 437.0 1006.0 422.0 2.6 132600.0 NEAR BAY -122.28 37.85 41.0 535.0 123.0 317.0 119.0 2.4038 107500.0 NEAR BAY -122.28 37.85 49.0 1130.0 244.0 607.0 239.0 2.4597 93800.0 NEAR BAY -122.28 37.85 52.0 1898.0 421.0 1102.0 397.0 1.808 105500.0 NEAR BAY -122.28 37.84 50.0 2082.0 492.0 1131.0 473.0 1.6424 108900.0 NEAR BAY -122.28 37.84 52.0 729.0 160.0 395.0 155.0 1.6875 132000.0 NEAR BAY -122.28 37.84 49.0 1916.0 447.0 863.0 378.0 1.9274 122300.0 NEAR BAY -122.28 37.84 52.0 2153.0 481.0 1168.0 441.0 1.9615 115200.0 NEAR BAY -122.27 37.84 48.0 1922.0 409.0 1026.0 335.0 1.7969 110400.0 NEAR BAY -122.27 37.83 49.0 1655.0 366.0 754.0 329.0 1.375 104900.0 NEAR BAY -122.27 37.83 51.0 2665.0 574.0 1258.0 536.0 2.7303 109700.0 NEAR BAY -122.27 37.83 49.0 1215.0 282.0 570.0 264.0 1.4861 97200.0 NEAR BAY -122.27 37.83 48.0 1798.0 432.0 987.0 374.0 1.0972 104500.0 NEAR BAY -122.28 37.83 52.0 1511.0 390.0 901.0 403.0 1.4103 103900.0 NEAR BAY -122.26 37.83 52.0 1470.0 330.0 689.0 309.0 3.48 191400.0 NEAR BAY -122.26 37.83 52.0 2432.0 715.0 1377.0 696.0 2.5898 176000.0 NEAR BAY -122.26 37.83 52.0 1665.0 419.0 946.0 395.0 2.0978 155400.0 NEAR BAY -122.26 37.83 51.0 936.0 311.0 517.0 249.0 1.2852 150000.0 NEAR BAY -122.26 37.84 49.0 713.0 202.0 462.0 189.0 1.025 118800.0 NEAR BAY -122.26 37.84 52.0 950.0 202.0 467.0 198.0 3.9643 188800.0 NEAR BAY -122.26 37.83 52.0 1443.0 311.0 660.0 292.0 3.0125 184400.0 NEAR BAY -122.26 37.83 52.0 1656.0 420.0 718.0 382.0 2.6768 182300.0 NEAR BAY -122.26 37.83 50.0 1125.0 322.0 616.0 304.0 2.026 142500.0 NEAR BAY -122.27 37.82 43.0 1007.0 312.0 558.0 253.0 1.7348 137500.0 NEAR BAY -122.26 37.82 40.0 624.0 195.0 423.0 160.0 0.9506 187500.0 NEAR BAY -122.27 37.82 40.0 946.0 375.0 700.0 352.0 1.775 112500.0 NEAR BAY -122.27 37.82 21.0 896.0 453.0 735.0 438.0 0.9218 171900.0 NEAR BAY -122.27 37.82 43.0 1868.0 456.0 1061.0 407.0 1.5045 93800.0 NEAR BAY -122.27 37.82 41.0 3221.0 853.0 1959.0 720.0 1.1108 97500.0 NEAR BAY -122.27 37.82 52.0 1630.0 456.0 1162.0 400.0 1.2475 104200.0 NEAR BAY -122.28 37.82 52.0 1170.0 235.0 701.0 233.0 1.6098 87500.0 NEAR BAY -122.28 37.82 52.0 945.0 243.0 576.0 220.0 1.4113 83100.0 NEAR BAY -122.28 37.82 5

In [0]:
print(f'shape={housing.count(), len(housing.columns)}')

shape=(20640, 10)


In [0]:
display(housing)

longitude latitude housing_median_age total_rooms total_bedrooms population households median_income median_house_value ocean_proximity -122.23 37.88 41.0 880.0 129.0 322.0 126.0 8.3252 452600.0 NEAR BAY -122.22 37.86 21.0 7099.0 1106.0 2401.0 1138.0 8.3014 358500.0 NEAR BAY -122.24 37.85 52.0 1467.0 190.0 496.0 177.0 7.2574 352100.0 NEAR BAY -122.25 37.85 52.0 1274.0 235.0 558.0 219.0 5.6431 341300.0 NEAR BAY -122.25 37.85 52.0 1627.0 280.0 565.0 259.0 3.8462 342200.0 NEAR BAY -122.25 37.85 52.0 919.0 213.0 413.0 193.0 4.0368 269700.0 NEAR BAY -122.25 37.84 52.0 2535.0 489.0 1094.0 514.0 3.6591 299200.0 NEAR BAY -122.25 37.84 52.0 3104.0 687.0 1157.0 647.0 3.12 241400.0 NEAR BAY -122.26 37.84 42.0 2555.0 665.0 1206.0 595.0 2.0804 226700.0 NEAR BAY -122.25 37.84 52.0 3549.0 707.0 1551.0 714.0 3.6912 261100.0 NEAR BAY -122.26 37.85 52.0 2202.0 434.0 910.0 402.0 3.2031 281500.0 NEAR BAY -122.26 37.85 52.0 3503.0 752.0 1504.0 734.0 3.2705 241800.0 NEAR BAY -122.26 37.85 52.0 2491.0 474.0 1098.0 468.0 3.075 213500.0 NEAR BAY -122.26 37.84 52.0 696.0 191.0 345.0 174.0 2.6736 191300.0 NEAR BAY -122.26 37.85 52.0 2643.0 626.0 1212.0 620.0 1.9167 159200.0 NEAR BAY -122.26 37.85 50.0 1120.0 283.0 697.0 264.0 2.125 140000.0 NEAR BAY -122.27 37.85 52.0 1966.0 347.0 793.0 331.0 2.775 152500.0 NEAR BAY -122.27 37.85 52.0 1228.0 293.0 648.0 303.0 2.1202 155500.0 NEAR BAY -122.26 37.84 50.0 2239.0 455.0 990.0 419.0 1.9911 158700.0 NEAR BAY -122.27 37.84 52.0 1503.0 298.0 690.0 275.0 2.6033 162900.0 NEAR BAY -122.27 37.85 40.0 751.0 184.0 409.0 166.0 1.3578 147500.0 NEAR BAY -122.27 37.85 42.0 1639.0 367.0 929.0 366.0 1.7135 159800.0 NEAR BAY -122.27 37.84 52.0 2436.0 541.0 1015.0 478.0 1.725 113900.0 NEAR BAY -122.27 37.84 52.0 1688.0 337.0 853.0 325.0 2.1806 99700.0 NEAR BAY -122.27 37.84 52.0 2224.0 437.0 1006.0 422.0 2.6 132600.0 NEAR BAY -122.28 37.85 41.0 535.0 123.0 317.0 119.0 2.4038 107500.0 NEAR BAY -122.28 37.85 49.0 1130.0 244.0 607.0 239.0 2.4597 93800.0 NEAR BAY -122.28 37.85 52.0 1898.0 421.0 1102.0 397.0 1.808 105500.0 NEAR BAY -122.28 37.84 50.0 2082.0 492.0 1131.0 473.0 1.6424 108900.0 NEAR BAY -122.28 37.84 52.0 729.0 160.0 395.0 155.0 1.6875 132000.0 NEAR BAY -122.28 37.84 49.0 1916.0 447.0 863.0 378.0 1.9274 122300.0 NEAR BAY -122.28 37.84 52.0 2153.0 481.0 1168.0 441.0 1.9615 115200.0 NEAR BAY -122.27 37.84 48.0 1922.0 409.0 1026.0 335.0 1.7969 110400.0 NEAR BAY -122.27 37.83 49.0 1655.0 366.0 754.0 329.0 1.375 104900.0 NEAR BAY -122.27 37.83 51.0 2665.0 574.0 1258.0 536.0 2.7303 109700.0 NEAR BAY -122.27 37.83 49.0 1215.0 282.0 570.0 264.0 1.4861 97200.0 NEAR BAY -122.27 37.83 48.0 1798.0 432.0 987.0 374.0 1.0972 104500.0 NEAR BAY -122.28 37.83 52.0 1511.0 390.0 901.0 403.0 1.4103 103900.0 NEAR BAY -122.26 37.83 52.0 1470.0 330.0 689.0 309.0 3.48 191400.0 NEAR BAY -122.26 37.83 52.0 2432.0 715.0 1377.0 696.0 2.5898 176000.0 NEAR BAY -122.26 37.83 52.0 1665.0 419.0 946.0 395.0 2.0978 155400.0 NEAR BAY -122.26 37.83 51.0 936.0 311.0 517.0 249.0 1.2852 150000.0 NEAR BAY -122.26 37.84 49.0 713.0 202.0 462.0 189.0 1.025 118800.0 NEAR BAY -122.26 37.84 52.0 950.0 202.0 467.0 198.0 3.9643 188800.0 NEAR BAY -122.26 37.83 52.0 1443.0 311.0 660.0 292.0 3.0125 184400.0 NEAR BAY -122.26 37.83 52.0 1656.0 420.0 718.0 382.0 2.6768 182300.0 NEAR BAY -122.26 37.83 50.0 1125.0 322.0 616.0 304.0 2.026 142500.0 NEAR BAY -122.27 37.82 43.0 1007.0 312.0 558.0 253.0 1.7348 137500.0 NEAR BAY -122.26 37.82 40.0 624.0 195.0 423.0 160.0 0.9506 187500.0 NEAR BAY -122.27 37.82 40.0 946.0 375.0 700.0 352.0 1.775 112500.0 NEAR BAY -122.27 37.82 21.0 896.0 453.0 735.0 438.0 0.9218 171900.0 NEAR BAY -122.27 37.82 43.0 1868.0 456.0 1061.0 407.0 1.5045 93800.0 NEAR BAY -122.27 37.82 41.0 3221.0 853.0 1959.0 720.0 1.1108 97500.0 NEAR BAY -122.27 37.82 52.0 1630.0 456.0 1162.0 400.0 1.2475 104200.0 NEAR BAY -122.28 37.82 52.0 1170.0 235.0 701.0 233.0 1.6098 87500.0 NEAR BAY -122.28 37.82 52.0 945.0 243.0 576.0 220.0 1.4113 83100.0 NEAR BAY -122.28 37.82 5

Databricks data profile. Run in Databricks to view.

# Data visualization